In [2]:
import numpy as np
import pandas as pd
from datetime import datetime, date
from utils_SA import simulate_model
import pypesto
import pypesto.optimize as optimize
import pypesto.visualize as visualize
import matplotlib.pyplot as plt
import time
import json

In [1]:
from inputFactorSpace import input_factor_names, lower_bounds, upper_bounds

In [3]:
path_data = 'data/worldometer_data.txt'

# Define Comartment names
compartments = ['susceptible', 'exposed', 'carrier', 'infected', 'hospitalized', 'icu', 'recovered', 'dead']
Compartments = ['Susceptible', 'Exposed', 'Carrier', 'Infected', 'Hospitalized', 'ICU', 'Recovered', 'Dead']
# Define age Groups
groups = ['0-4', '5-14', '15-34', '35-59', '60-79', '80+']
# Define population of age groups
populations = [40000, 70000, 190000, 290000, 180000, 60000] 

days = 50 # number of days to simulate
output_index = 7

start_day = 18
start_month = 3
start_year = 2020
starting_day = (date(start_year, start_month, start_day) - date(start_year, 1, 1)).days
dt = 0.1
num_groups = len(groups)
num_compartments = len(compartments)

static_params = {
    'num_groups': num_groups, 
    'num_compartments': num_compartments,
    'populations': populations,
    'start_day' : (date(start_year, start_month, start_day) - date(start_year, 1, 1)).days,
    'days' : days,
    'dt' : dt,
    # which compartment's value should be outputed?
    'output_index' : output_index #compartments.index("Dead")
}

In [4]:
# load data
data_dict = {}
with open(path_data) as f:
    lines = f.readlines()
    #data_dict.update(lines[0])
    print(lines[-1])
    for i in range(len(lines)-1):
        (key, value) = lines[i].split(":")
        value = json.loads(value)
        data_dict[key] = value
print(data_dict.keys())

start_dataset = 32
number_of_days = days
print(data_dict['categories'][start_dataset])
print(start_year, start_month, start_day)

# when used for a different time period, initial numbers must be matched first. 
# Saved simulation is from start day 0, therefore no initial numbers in Hospitalized, Infected and Recovered
# Divide by 100 because of the population size used in the model
#dataset = np.zeros((number_of_days+1, 2))
#dataset[:, 0] = np.array(data_dict['currently_infected'][start_dataset:number_of_days+1+start_dataset])/100.0
#dataset[:, 1] = np.array(data_dict['total_deaths'][start_dataset:number_of_days+1+start_dataset])/100.0

dead_cases = np.array(data_dict['total_deaths'][start_dataset:number_of_days+1+start_dataset])/100.0
infected_cases = np.array(data_dict['currently_infected'][start_dataset:number_of_days+1+start_dataset])/100.0

source : "https://www.worldometers.info/coronavirus/country/germany/#graph-deaths-daily"

dict_keys(['categories', 'currently_infected', 'total_deaths', 'new_recoveries'])
Mar 18, 2020
2020 3 18


In [29]:
# load file for parameter importance
df_fixing = pd.read_csv('results/dgsm_vi_important.csv', index_col = 0)
#df_fixing.rename(columns = {'vi': 'fix'})

In [31]:
factors_to_fix = [df_fixing.loc[name, 'vi'] for name in input_factor_names]
def fix_factors(input_factor_names) 

In [14]:

def simulate_model_logParam(theta, 
                            param_names = input_factor_names, 
                            static_params = static_params):
    '''
    Call the model simulation for given log-transformed 
    values (theta) for the parameters listed in param_names. 
    The static parameters include all other parameters that are not
    subject to the optimization.
    '''
    theta = np.exp(theta)
    result = simulate_model({**static_params, **dict(zip(param_names, theta))})
    return result


# TODO: change noise model
def neg_log_likelihood_logParam(theta, measurement = infected_cases):
    sigma = theta[0]
    simulation = simulate_model_logParam(theta[1:])
    simulation = np.cumsum(simulation)
    nllh = np.log(2*np.pi*sigma**2)+((measurement-simulation)/sigma)**2
    nllh = 0.5*sum(nllh)
    return nllh

def neg_binomial_log_likelihood():
    '''
    Discrete distribution that models nb of successes in a sequence of iid Bernoulli trials
    before r predefinded events (failures) occur. 
    Suitable if used to model the nb of infected/ pos. tested individuals as the event rate
    is known but the number of test is usually not.
    (Bernoulli trials: COVID tests, success: negative test, failure: positive test)
    r > 0 (int): number of failures until the experiment is stopped
    p in [0, 1] (float): success probability in each experiment
    '''
    return


In [17]:
#----------------------------------------------------------------------------------------------------------------------------------------------

objective1 = pypesto.Objective(
    fun=neg_log_likelihood_logParam,
)

# set upper and lower bound
#lb = np.array([1e-3] + [50, 25, 10, 10, 1e-3, 1e-3, 1e-3] + [3, 1, 1, 1, 1, 1] + [0.1, 0.6, 0.05, 0.01, 0.1, 0.15, 0.15, 1])
#ub = np.array([1] + [150, 75, 30, 30, 20, 20, 1] + [7, 15, 15, 15, 15, 15] + [ 0.9, 1.0, 0.5, 0.16, 0.35, 0.4, 0.77, 3])

lb = np.array([1e-5] + lower_bounds)
lb = np.where(lb <= 0, 1e-9, lb)
ub = np.array([1] + upper_bounds)#+1e-9 

lb = np.log(lb)
ub = np.log(ub)

problem1 = pypesto.Problem(objective=objective1, lb=lb, ub=ub)

# create different optimizers
optimizer_bfgs = optimize.ScipyOptimizer(method="l-bfgs-b")
optimizer_tnc = optimize.ScipyOptimizer(method="TNC")

# set number of starts
n_starts = 15
# save optimizer trace
history_options = pypesto.HistoryOptions(trace_record=True)

start = time.time()
# Run optimizaitons for different optimzers
# result1_bfgs = optimize.minimize(
#     problem=problem1,
#     optimizer=optimizer_bfgs,
#     n_starts=n_starts,
#     history_options=history_options,
#     filename=None,
# )

result1_tnc = optimize.minimize(
    problem=problem1,
    optimizer=optimizer_tnc,
    n_starts=n_starts,
    history_options=history_options,
    filename='logs/'+ time.strftime("%Y-%m-%d %H%M%S") + '_optimizer_log.hdf5',
)

end = time.time()


  0%|                                                    | 0/15 [00:00<?, ?it/s]

[2022-09-03 17:02:48.943] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.952] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.959] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.964] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.969] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.974] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.979] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.984] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.989] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.994] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:48.999] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.004] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.008] [info] Adaptiv

[2022-09-03 17:02:49.571] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.575] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.578] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.582] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.586] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.590] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.594] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.598] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.602] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.605] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.609] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.613] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.617] [info] Adaptiv

[2022-09-03 17:02:49.986] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.990] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.993] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:49.997] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.001] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.005] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.009] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.013] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.017] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.021] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.025] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.029] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.032] [info] Adaptiv

[2022-09-03 17:02:50.395] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.399] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.403] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.407] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.411] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.414] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.418] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.422] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.426] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.430] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.434] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.438] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:02:50.442] [info] Adaptiv

...

[2022-09-03 17:05:55.431] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.435] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.439] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.443] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.447] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.451] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.455] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.459] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.463] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.467] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.471] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.475] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:55.479] [info] Adaptiv

[2022-09-03 17:05:56.051] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.056] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.061] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.065] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.070] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.074] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.079] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.084] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.089] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.093] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.098] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.102] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.107] [info] Adaptiv

  7%|██▊                                        | 1/15 [03:07<43:45, 187.57s/it]

[2022-09-03 17:05:56.460] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.465] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.469] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.473] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.477] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.481] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.486] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.490] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.495] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.499] [info] Adaptive step sizing successful to tolerances.
[2022-09-03 17:05:56.503] [info] Adaptive step sizing successful to tolerances.


KeyboardInterrupt: 

In [ ]:
print("It needed ", end - start, " seconds.")
#print("BFGS")
#print((result1_bfgs.optimize_result.as_list()))
print("TNC")
print((result1_tnc.optimize_result.as_list()))
print("Data_____________________________")
print(result1_tnc.optimize_result.as_list()[0]['x'])
print(len(result1_tnc.optimize_result.as_list()[0]['x']))

In [ ]:
from inputFactorSpace import input_factor_names, coll

parser = argparse.ArgumentParser(description='Setup of the experiment parameters for sampling to visualize S_i.')
parser.add_argument('--MC_size_outer', '-no', help="outer sample size", type=int, default = 10)
parser.add_argument('--MC_size_inner', '-ni', help="inner sample size", type=int, default = 100)
parser.add_argument('--output_index', '-oi', help="index of compartment(s) for model output", type= int, nargs='+')

args = parser.parse_args()
N_inner = args.MC_size_inner
N_outer = args.MC_size_outer
output_index = args.output_index



In [ ]:
# Define Comartment names
compartments = ['Susceptible', 'Exposed', 'Carrier', 'Infected', 'Hospitalized', 'ICU', 'Recovered', 'Dead']
# Define age Groups
groups = ['0-4', '5-14', '15-34', '35-59', '60-79', '80+']
# Define population of age groups
populations = [40000, 70000, 190000, 290000, 180000, 60000] 


static_params["output_operation"]= "all" #"max"

input_factor_i = 'deaths_per_ICU_5' #'serial_interval'
i = input_factor_names.index(input_factor_i)

##set coll ot distribution of X_{~i}
# remove name from list
input_factor_names.pop(i)
# distribution of X_{~i}, pop returns distribution of factor i
dist_i = coll.pop(i)

inputDistribution = ot.ComposedDistribution(coll)
inputDistribution.setDescription(input_factor_names)

ot.RandomGenerator.SetSeed(0)
# create random points for all factors except i
# random point for for all factors except i
N_outer = 10
MCexperiment = ot.MonteCarloExperiment(inputDistribution, N_outer)

MCinputDesign = MCexperiment.generate()
MCinputDesign.setDescription(input_factor_names)

N_inner = 100
#N = len(MCinputDesign)

print(f"Computed {N_outer} MC samples for all but input factor i.")

outs = []
for n in range(N_outer):
    fixed_params_n = dict(zip(input_factor_names, MCinputDesign[n]))
    MCexperiment_i = ot.MonteCarloExperiment(dist_i, N_inner)
    # sample input factor i
    MCinputDesign_i = MCexperiment_i.generate()
    print(len(MCinputDesign_i))
    print(type(MCinputDesign_i))
    # simulate model on different samples for i, other values fixed
    sim_out = generate_output_daywise_one_factor(MCinputDesign_i, input_factor_i, {**static_params, **fixed_params_n})
    # save value of last day
    outs.append(sim_out[:, -1])
print(f"Computed {N_outer} times {len(outs[0])} MC samples for input factor i.")

saving_path = f'Studies/MC_{input_factor_i}_{N_outer}_{N_inner}_{"".join(compartments[i] for i in output_index)}.pkl'
print(f"Study is saved to {saving_path}.")

with open(saving_path, 'wb') as f:
    pickle.dump(N_outer, f)
    pickle.dump(N_inner, f)
    pickle.dump(input_factor_names, f)
    pickle.dump(coll, f)
    pickle.dump(static_params, f)
    pickle.dump(input_factor_i, f)
    pickle.dump(dist_i, f)
    pickle.dump(outs, f)


